In [2]:
USE_GPU = False
from typing import List, Tuple, Dict, Any, Optional
import seaborn as sns
from sklearn.metrics import roc_auc_score, accuracy_score, precision_score, recall_score, f1_score
import statsmodels.api as sm
import re
import plotly.express as px
import pandas as pd
import numpy as np
import seaborn as sns
from tensorboard.backend.event_processing.event_accumulator import EventAccumulator
import matplotlib.pyplot as plt
import os
import glob
from typing import Dict
from statsmodels.tsa.filters.hp_filter import hpfilter
import re
from datetime import datetime
import plotly
import plotly.offline as pyo
import plotly.io as pio

from plotly.subplots import make_subplots
import plotly.graph_objects as go

pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)
pd.set_option('display.max_rows', 500)
pd.set_option('mode.chained_assignment', None)
pio.renderers.default = 'notebook+pdf'

PLOTLY_COLORS = plotly.colors.DEFAULT_PLOTLY_COLORS

In [3]:
def review_distribution_incentives(policy_list, segment):
    policy_matrix = {}
    for policy_name, file_loc in policy_list.items():
        df = pd.read_csv(file_loc)
        if segment:
            df = df[(
                (df['session_size'] >= segment[0]) &
                (df['session_size'] <= segment[1])
            )]
        df =df[df['ended_event'] > 0]
        policy_matrix[policy_name] = df
    
    return policy_matrix

def policy_matrix(policies):
    for policy, results_subset in policies.items():
        print(f'Loading policies with {results_subset.keys()}')
        train_df, eval_df = pd.read_parquet(results_subset['train']), pd.read_parquet(results_subset['eval'])
        policies[policy]['train'] = train_df
        policies[policy]['eval'] = eval_df
    
    return policies

def plot_cutoffs(df_subset, cols):

    incentive_df = pd.melt(df_subset, id_vars=['size_cutoff', 'ended_event', 'session_size', 'Completed'], value_vars=['inc_small', 'inc_medium', 'inc_large'])
    return incentive_df.rename({'variable': 'incentive', 'value': 'inc_loc'}, axis=1)


def _session_subset(x):
    if x <= 20:
        return 'small'
    
    if x >= 20 and x <= 40:
        return 'mid'

    if x >= 40 and x <= 60:
        return 'large'

    return 'max'
def generate_subsets(policy_matrix):
    
    for policy, results_subset in policy_matrix.items():
        
        results_subset_train, results_subset_eval = results_subset['train'], results_subset['eval']
        
        results_subset_train['size_subset'] = results_subset_train['session_size'].apply(_session_subset)
        results_subset_eval['size_subset'] = results_subset_eval['session_size'].apply(_session_subset)
        results_subset_train['Completed'] = results_subset_train['ended_event'] / results_subset_train['session_size']
        results_subset_eval['Completed'] = results_subset_eval['ended_event'] / results_subset_eval['session_size']
        
    
        policy_matrix[policy]['train'] = results_subset_train
        policy_matrix[policy]['eval'] = results_subset_eval

        
    return policy_matrix



def create_incentive_scattergraph(df, title_suffix):

    fig_sub = px.scatter(df, y='inc_loc', x='Completed', color='incentive', symbol='incentive', facet_col='subset', facet_row='dataset')
    fig_sub.update_xaxes(matches=None)
    fig_sub.update_yaxes(matches=None, showticklabels=True)
    fig_sub.update_layout(
        title=f'Distribution of Incentives and Session Contributions Training And Validation Set for DQN {title_suffix}',
        scattermode='group',
        scattergap=0
    )
    
    fig_sub.show()

def concatenate_policy_dfs(policy_train, policy_eval):
    df_train = generate_subsets(policy_train)
    df_eval = generate_subsets(policy_eval)
    
    df_train['dataset'] = 'train'
    df_eval['dataset'] = 'eval'
    
    df = pd.concat([df_train, df_eval], axis=0)
    return df


def compare_statistics(df_matrix):
    summary_container = []
    for df in df_matrix:
        summary_container.append(
            df.groupby(['size_subset', 'dataset', 'policy'])['Completed'].mean().reset_index()
        )
    

    summary_stats_df = pd.concat(summary_container, axis=0)
    return summary_stats_df

def compare_incentive_utilization(df_matrix):
    summary_container = []
    
    for df in df_matrix:
        df['inc_placed'] = df['inc_loc'].apply(lambda x: 1 if x > 0 else 0)
        df = df.groupby(['subset', 'dataset', 'policy', 'incentive']).agg({'inc_placed': 'sum', 'inc_loc': 'count'}).reset_index()
        df['inc_utilization'] = df['inc_placed'] / df['inc_loc']
        summary_container.append(df)
    
    summary_stats = pd.concat(summary_container, axis=0)
    return summary_stats


def plot_3d_scatter(df_container, title):
    
    subplots = make_subplots(
        rows=1, 
        cols=2, 
        specs=[[ {'type': 'scatter3d'}, {'type': 'scatter3d'}]],
        subplot_titles=['Val Prediction', 'Val No Prediction'],
        vertical_spacing=1,
        horizontal_spacing=0.05,
    )    
    for df, loc in zip(df_container, [(1, 1), (1, 2)]):
        subplots.add_trace(
            go.Scatter3d(
                x=df['inc_small'],
                y=df['inc_medium'],
                z=df['inc_large'],
                mode='markers',
                marker=dict(
                    color=df['Completed'],
                    colorscale='Viridis',
                    opacity=0.8,
                showscale = True if loc == (1, 1) else False
                # showscale=True,
            ),
        ),
        row=loc[0],
        col=loc[1]
    )
    
    subplots.update_layout(
        width=2000,
        height=1000,
        title=title,
        showlegend=True,

    )
    
    subplots.update_scenes(
        xaxis_title_text='S Loc',
        yaxis_title_text='M Loc',
        zaxis_title_text='L Loc',
    )
    subplots.show()
    
    title = re.sub('[^A-Za-z0-9]+', '', title)
    subplots.write_image('rl_plots/3d_scatter_{}.png'.format(title))

In [4]:
POLICIES = {
    'DQN PRED CNN NO PEN': {
        'train': 'dqn_parquet/train/dqn_pred_cnn_25000_no_pen.parquet',
        'eval': 'dqn_parquet/eval/dqn_pred_cnn_15000_no_pen.parquet'
    },
    'DQN NONE CNN NO Pen': {
        'train': 'dqn_parquet/train/dqn_None_cnn_25000_no_pen.parquet',
        'eval': 'dqn_parquet/eval/dqn_None_cnn_15000_no_pen.parquet'
    }
}

SEGMENTATIONS = [
    (0, 20)
]


In [5]:
policy_loaded = policy_matrix(POLICIES.copy())
policy_segmented = generate_subsets(policy_loaded.copy())
train_pred, eval_pred = policy_segmented['DQN PRED CNN NO PEN']['train'], policy_segmented['DQN PRED CNN NO PEN']['eval']
train_none, eval_none = policy_segmented['DQN NONE CNN NO Pen']['train'], policy_segmented['DQN NONE CNN NO Pen']['eval']

Loading policies with dict_keys(['train', 'eval'])
Loading policies with dict_keys(['train', 'eval'])


In [6]:
train_pred_s, val_pred_s = train_pred[train_pred['size_subset'] == 'small'], eval_pred[eval_pred['size_subset'] == 'small']
train_none_s, val_none_s = train_none[train_none['size_subset'] == 'small'], eval_none[eval_none['size_subset'] == 'small']
plot_3d_scatter([ val_pred_s, val_none_s], 'Small Session Size')

In [19]:
train_pred_m, val_pred_m = train_pred[train_pred['size_subset'] == 'mid'], eval_pred[eval_pred['size_subset'] == 'mid']
train_none_m, val_none_m = train_none[train_none['size_subset'] == 'mid'], eval_none[eval_none['size_subset'] == 'mid']
plot_3d_scatter([val_pred_m, val_none_m], 'Medium Session Size')

In [20]:
train_pred_l, val_pred_l = train_pred[train_pred['size_subset'] == 'large'], eval_pred[eval_pred['size_subset'] == 'large']
train_none_l, val_none_l = train_none[train_none['size_subset'] == 'large'], eval_none[eval_none['size_subset'] == 'large']
plot_3d_scatter([train_none_l, val_none_l], 'Large Session Size')

In [21]:
train_pred_ma, val_pred_ma = train_pred[train_pred['size_subset'] == 'max'], eval_pred[eval_pred['size_subset'] == 'max']
train_none_ma, val_none_ma = train_none[train_none['size_subset'] == 'max'], eval_none[eval_none['size_subset'] == 'max']
plot_3d_scatter([train_none_ma, val_none_ma], 'Max Session Size')

In [22]:
train_pred['dataset'] = 'train'
eval_pred['dataset'] = 'eval'

train_none['dataset'] = 'train'
eval_none['dataset'] = 'eval'

pred = pd.concat([train_pred, eval_pred], axis=0)
pred['policy'] = 'DQN PRED CNN'

none = pd.concat([train_none, eval_none], axis=0)
none['policy'] = 'DQN NONE CNN'

completed_summary = compare_statistics([pred, none])

completed_summary.head()

fig = px.bar(completed_summary, x='size_subset', y='Completed', color='dataset', barmode='group', facet_col='policy')

fig.write_image('rl_plots/q1/completed_summary_comp_end.png')

fig.show()

In [24]:
inc_util_df = pd.concat([pred, none], axis=0)
inc_util_df['small'] = inc_util_df['inc_small'].apply(lambda x: 1 if x > 0 else 0)
inc_util_df['mid'] = inc_util_df['inc_medium'].apply(lambda x: 1 if x > 0 else 0)
inc_util_df['large'] = inc_util_df['inc_large'].apply(lambda x: 1 if x > 0 else 0)


inc_util_grouper = inc_util_df.groupby(['policy', 'size_subset', 'dataset']).agg({'small': 'sum', 'mid': 'sum', 'large': 'sum', 'inc_small': 'count', 'inc_medium': 'count', 'inc_large': 'count'}).reset_index()

inc_util_grouper['small inc'] = inc_util_grouper['small'] / inc_util_grouper['inc_small']
inc_util_grouper['mid inc'] = inc_util_grouper['mid'] / inc_util_grouper['inc_medium']
inc_util_grouper['large inc'] = inc_util_grouper['large'] / inc_util_grouper['inc_large']

inc_util_grouper = inc_util_grouper.drop(columns=['small', 'mid', 'large', 'inc_small', 'inc_medium', 'inc_large'])
inc_util_grouper.head()

inc_util_grouper_melted = pd.melt(inc_util_grouper, id_vars=['policy', 'size_subset', 'dataset'], value_vars=['small inc', 'mid inc', 'large inc' ]).rename(columns={'variable': 'incentive', 'value': 'percent applied'})
inc_util_grouper_melted['size_subset'] = inc_util_grouper_melted['size_subset'].apply(lambda x: x if x != 'max' else 'top')
inc_util_grouper = inc_util_grouper_melted.sort_values(by=['size_subset', 'policy', 'incentive'])
# inc_util_grouper_melted.head(

In [25]:
fig = px.bar(inc_util_grouper_melted, x='size_subset', y='percent applied', color='incentive', facet_col='policy', facet_row='dataset', barmode='group')
fig.write_image('rl_plots/q1/completed_summary_inc_used.png')

fig.show()